In [1]:
import random
import plotly.graph_objects as go
import plotly.express as px
import pandas as pd
from pandas import DataFrame
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn import metrics
import numpy as np
from scipy import stats
from datetime import datetime
from sklearn import preprocessing
from sklearn.model_selection import KFold
from sklearn.linear_model import LinearRegression
import matplotlib.pyplot as plt

randomlist = []
for i in range(0,1000): #pulling random numbers for yield
    n = random.randint(150,275)
    randomlist.append(n)

randomlist2 = []
for i in range(0,1000): #pulling random numbers for price
    n = round(random.uniform(2.50,7),2)
    randomlist2.append(n)

data = DataFrame(randomlist,columns = ['Yield'])
data['Price'] = randomlist2

data['Revenue'] = data['Yield']*data['Price']

data

Yield  Price  Revenue
0      245   2.82   690.90
1      241   5.29  1274.89
2      271   6.21  1682.91
3      156   4.09   638.04
4      189   5.84  1103.76
..     ...    ...      ...
995    258   4.02  1037.16
996    178   3.33   592.74
997    274   3.16   865.84
998    230   3.66   841.80
999    164   4.67   765.88

[1000 rows x 3 columns]

In [2]:
c_data = pd.read_csv('/Users/isaacwerries/Desktop/542 Data.csv')
ci_price = pd.read_csv('/Users/isaacwerries/Desktop/CI Prices.csv')

del c_data['Program'], c_data['Week Ending'], c_data['Zip Code'], c_data['Region'], c_data['watershed_code'],c_data['Domain'], c_data['Domain Category'], c_data['Geo Level'], c_data['State ANSI'], c_data['Ag District'], c_data['Ag District Code'],c_data['Watershed']
corn = c_data[c_data['Commodity'] == 'CORN'] #splitting the dataframe based on crop
corn = corn[corn['Year'] > 2000].copy()
beans = c_data[c_data['Commodity'] == 'SOYBEANS'] #splitting the dataframe based on crop
beans = beans[beans['Year'] > 2000].copy()

In [3]:
#Linear Regression for corn
cornx = np.array(corn['Value']).reshape((-1,1))
corny = np.array(corn['Year']).reshape((-1,1))
corny.reshape((-1,1))
lr = LinearRegression()
regress = lr.fit(corny,cornx)
cinter = regress.intercept_ #intercept
cslope = regress.coef_ #slope

In [4]:
cinter = cinter[0]
cinter

-4858.711407747956

In [5]:
cslope = cslope[0]
cslope

array([2.49784023])

# Corn:

In [6]:
ci = pd.read_csv('/Users/isaacwerries/Desktop/CI Prices.csv')
corn = pd.merge(ci,corn)

In [7]:
corn['Trend fitted yield'] = corn['Year']*cslope+cinter
corn['Trend adjusted yield'] = corn['Value']+cslope*(2020-corn['Year'])
corn['Random Price'] = [round(random.uniform(2.50,7),2) for k in corn.index]
corn['Revenue'] = corn['Random Price']*corn['Trend adjusted yield']
corn = pd.merge(ci_price,corn)
del corn['Beans Base Price'], corn['Beans Harvest Price']
aph1 = corn.groupby(['County'])['Value'].agg(['sum','count']).reset_index()
corn = pd.merge(corn,aph1)
corn['County APH'] = ((corn['sum'])/(corn['count']))
corn['bp guarantee'] = corn['Trend adjusted yield']*corn['Corn Base Price']
corn['hp guarantee'] = corn['Trend adjusted yield']*corn['Corn Harvest Price']
corn['Revenue Guarantee 75%'] = corn[['bp guarantee','hp guarantee']].max(axis = 1)*.75
corn['Revenue Guarantee 80%'] = corn[['bp guarantee','hp guarantee']].max(axis = 1)*.8
corn['Revenue Guarantee 85%'] = corn[['bp guarantee','hp guarantee']].max(axis = 1)*.85
corn['0'] = 0
corn['75% dif'] = corn['Revenue Guarantee 75%']-corn['Revenue']
corn['80% dif'] = corn['Revenue Guarantee 80%']-corn['Revenue']
corn['85% dif'] = corn['Revenue Guarantee 85%']-corn['Revenue']
corn['75% payout'] = corn[['75% dif','0']].max(axis = 1)
corn['80% payout'] = corn[['80% dif','0']].max(axis = 1)
corn['85% payout'] = corn[['85% dif','0']].max(axis = 1)
corn['75% Revenue'] = corn['75% payout']+corn['Revenue']
corn['80% Revenue'] = corn['80% payout']+corn['Revenue']
corn['85% Revenue'] = corn['85% payout']+corn['Revenue']
corn.head()

Year  Corn Base Price  Corn Harvest Price Period     State   County  \
0  2001             2.46                2.05   YEAR  ILLINOIS  DE WITT   
1  2002             2.32                2.52   YEAR  ILLINOIS  DE WITT   
2  2003             2.42                2.37   YEAR  ILLINOIS  DE WITT   
3  2004             2.83                1.99   YEAR  ILLINOIS  DE WITT   
4  2005             2.32                1.93   YEAR  ILLINOIS  DE WITT   

   County ANSI Commodity                                   Data Item  Value  \
0         39.0      CORN  CORN, GRAIN - YIELD, MEASURED IN BU / ACRE  158.0   
1         39.0      CORN  CORN, GRAIN - YIELD, MEASURED IN BU / ACRE  133.0   
2         39.0      CORN  CORN, GRAIN - YIELD, MEASURED IN BU / ACRE  181.0   
3         39.0      CORN  CORN, GRAIN - YIELD, MEASURED IN BU / ACRE  181.0   
4         39.0      CORN  CORN, GRAIN - YIELD, MEASURED IN BU / ACRE  162.0   

   ...  0     75% dif     80% dif     85% dif  75% payout  80% payout  \
0  ...  0 -368.798841 -343.527388 -318.255936         0.0         0.0   
1  ...  0 -512.528037 -490.104936 -467.681834         0.0         0.0   
2  ...  0 -908.378249 -881.339191 -854.300134         0.0         0.0   
3  ...  0 -516.506724 -485.240114 -453.973504         0.0         0.0   
4  ...  0 -763.960921 -740.822679 -717.684437         0.0         0.0   

   85% payout  75% Revenue  80% Revenue  85% Revenue  
0         0.0   747.870630   747.870630   747.870630  
1         0.0   848.874562   848.874562   848.874562  
2         0.0  1313.964109  1313.964109  1313.964109  
3         0.0   985.505878   985.505878   985.505878  
4         0.0  1111.034551  1111.034551  1111.034551  

[5 rows x 33 columns]

In [8]:
counties = corn.County.unique()
randomlist3 = []
randomlist4 = []
rand_yield = pd.DataFrame()
for n in counties:
    for i in range(0,1000): #pulling random numbers for yield
        test = corn[corn['County'] == n]
        aph3 = test['County APH']
        b = list(aph3.astype(int))
        j = round(random.uniform(b[0]-20,b[0]+20),2)
        randomlist3.append(j)
    rand_yield[n] = randomlist3
    randomlist3.clear()

rand_yield.head()

DE WITT   LOGAN   MACON  MARSHALL   MASON  MCLEAN  MENARD  PEORIA   STARK  \
0   167.38  170.32  186.73    177.62  160.37  169.26  172.01  188.23  202.51   
1   174.10  181.30  193.74    198.37  174.47  196.35  163.25  185.15  171.83   
2   176.57  182.60  171.94    177.43  180.81  195.25  191.27  194.84  195.88   
3   174.58  166.39  178.57    182.68  176.27  201.17  191.58  175.11  181.57   
4   181.75  193.69  169.92    199.38  155.99  187.77  188.55  201.80  205.20   

   TAZEWELL  ...  JERSEY  MACOUPIN  MADISON  MONTGOMERY  MORGAN    PIKE  \
0    194.14  ...  172.93    151.57   161.01      170.41  190.92  176.50   
1    184.19  ...  143.90    158.14   152.16      159.40  167.69  175.09   
2    183.02  ...  176.89    162.57   141.06      185.94  201.23  172.58   
3    169.98  ...  178.12    177.22   165.02      171.89  173.00  172.81   
4    200.63  ...  151.92    166.32   169.90      171.00  191.05  174.85   

   SANGAMON   SCOTT  OTHER (COMBINED) COUNTIES  OTHER COUNTIES  
0    206.94  169.36                     162.51          166.02  
1    183.19  176.84                     136.91          173.60  
2    168.15  149.42                     140.22          172.15  
3    200.14  157.56                     149.13          170.36  
4    195.35  181.64                     160.89          138.51  

[5 rows x 104 columns]

In [9]:
rand_price = pd.DataFrame()
for n in counties:
    for i in range(0,1000): #pulling random numbers for yield
        test = corn[corn['County'] == n]
        aph3 = test['Corn Base Price']
        sum = aph3.sum()
        b = list(aph3.astype(int))
        avg = sum/len(aph3)
        avg = avg.astype(int)
        j = round(random.uniform(avg-1.5,avg+1.5),2)
        randomlist3.append(j)
    rand_price[n] = randomlist3
    randomlist3.clear()

rand_price.head()

DE WITT  LOGAN  MACON  MARSHALL  MASON  MCLEAN  MENARD  PEORIA  STARK  \
0     4.35   2.36   3.51      4.21   4.42    2.97    1.87    4.25   3.16   
1     3.44   3.82   3.49      3.35   2.71    1.63    2.02    2.58   2.48   
2     1.85   2.93   3.33      2.02   2.12    3.67    2.50    4.31   3.42   
3     4.43   3.54   2.25      4.08   3.18    3.47    3.47    3.26   2.44   
4     2.03   4.22   4.44      4.04   3.26    1.66    2.97    2.29   2.99   

   TAZEWELL  ...  JERSEY  MACOUPIN  MADISON  MONTGOMERY  MORGAN  PIKE  \
0      3.03  ...    3.26      1.65     3.32        2.89    3.63  1.83   
1      1.87  ...    4.24      1.59     3.43        2.96    2.15  4.14   
2      3.31  ...    3.15      3.52     4.49        2.29    3.23  1.76   
3      4.17  ...    1.80      2.91     1.73        1.86    4.26  1.77   
4      3.80  ...    3.24      4.47     3.95        3.07    1.75  2.98   

   SANGAMON  SCOTT  OTHER (COMBINED) COUNTIES  OTHER COUNTIES  
0      3.62   2.73                       3.64            3.30  
1      4.36   3.64                       3.38            2.10  
2      3.08   3.43                       2.82            4.43  
3      3.76   4.07                       4.51            3.61  
4      2.03   2.80                       4.09            3.27  

[5 rows x 104 columns]

In [10]:
rev_ex = rand_price*rand_yield
rev_ex.head()

DE WITT     LOGAN     MACON  MARSHALL     MASON    MCLEAN    MENARD  \
0  728.1030  401.9552  655.4223  747.7802  708.8354  502.7022  321.6587   
1  598.9040  692.5660  676.1526  664.5395  472.8137  320.0505  329.7650   
2  326.6545  535.0180  572.5602  358.4086  383.3172  716.5675  478.1750   
3  773.3894  589.0206  401.7825  745.3344  560.5386  698.0599  664.7826   
4  368.9525  817.3718  754.4448  805.4952  508.5274  311.6982  559.9935   

     PEORIA     STARK  TAZEWELL  ...    JERSEY  MACOUPIN   MADISON  \
0  799.9775  639.9316  588.2442  ...  563.7518  250.0905  534.5532   
1  477.6870  426.1384  344.4353  ...  610.1360  251.4426  521.9088   
2  839.7604  669.9096  605.7962  ...  557.2035  572.2464  633.3594   
3  570.8586  443.0308  708.8166  ...  320.6160  515.7102  285.4846   
4  462.1220  613.5480  762.3940  ...  492.2208  743.4504  671.1050   

   MONTGOMERY    MORGAN      PIKE  SANGAMON     SCOTT  \
0    492.4849  693.0396  322.9950  749.1228  462.3528   
1    471.8240  360.5335  724.8726  798.7084  643.6976   
2    425.8026  649.9729  303.7408  517.9020  512.5106   
3    319.7154  736.9800  305.8737  752.5264  641.2692   
4    524.9700  334.3375  521.0530  396.5605  508.5920   

   OTHER (COMBINED) COUNTIES  OTHER COUNTIES  
0                   591.5364        547.8660  
1                   462.7558        364.5600  
2                   395.4204        762.6245  
3                   672.5763        614.9996  
4                   658.0401        452.9277  

[5 rows x 104 columns]

In [11]:
randomlist5 = []
cbase = pd.DataFrame()
for n in counties:
    for i in range(0,1000): #pulling random numbers for yield
        test = corn[corn['County'] == n]
        aph3 = test['Corn Base Price']
        b = list(aph3)
        j = random.choices(b)
        randomlist5.append(j[0])
    cbase[n] = randomlist5
    randomlist5.clear()
cbase.head()

DE WITT  LOGAN  MACON  MARSHALL  MASON  MCLEAN  MENARD  PEORIA  STARK  \
0     5.68   4.00   2.83      5.40   2.59    5.40    6.01    4.62   3.96   
1     4.15   4.00   3.99      3.97   4.06    2.83    2.59    3.88   2.42   
2     4.04   3.97   3.96      5.68   2.46    4.62    4.62    3.86   2.32   
3     3.96   4.06   3.99      4.06   5.68    2.59    2.83    3.96   3.97   
4     2.59   5.68   2.59      3.86   3.86    4.62    2.32    3.97   4.62   

   TAZEWELL  ...  JERSEY  MACOUPIN  MADISON  MONTGOMERY  MORGAN  PIKE  \
0      4.15  ...    4.04      2.32     2.83        6.01    2.46  5.65   
1      2.83  ...    4.62      4.06     2.42        5.40    5.68  2.46   
2      3.88  ...    3.88      4.06     3.86        3.86    5.68  5.65   
3      6.01  ...    2.32      5.68     3.86        4.06    3.97  6.01   
4      5.40  ...    2.83      6.01     2.32        4.06    3.99  2.32   

   SANGAMON  SCOTT  OTHER (COMBINED) COUNTIES  OTHER COUNTIES  
0      2.46   4.04                       5.65            3.88  
1      2.59   3.86                       4.00            3.88  
2      3.96   3.86                       3.96            3.88  
3      2.32   5.40                       5.68            3.88  
4      4.06   2.83                       5.65            3.88  

[5 rows x 104 columns]

In [12]:
randomlist5 = []
caph = pd.DataFrame()
for n in counties:
    for i in range(0,1000): #pulling random numbers for yield
        test = corn[corn['County'] == n]
        aph3 = test['County APH']
        b = list(aph3)
        j = b[0]
        randomlist5.append(j)
    caph[n] = randomlist5
    randomlist5.clear()
caph.head()

DE WITT   LOGAN    MACON  MARSHALL       MASON  MCLEAN      MENARD  \
0  182.838889  183.49  187.635   182.435  163.652632  185.03  178.976471   
1  182.838889  183.49  187.635   182.435  163.652632  185.03  178.976471   
2  182.838889  183.49  187.635   182.435  163.652632  185.03  178.976471   
3  182.838889  183.49  187.635   182.435  163.652632  185.03  178.976471   
4  182.838889  183.49  187.635   182.435  163.652632  185.03  178.976471   

   PEORIA    STARK  TAZEWELL  ...      JERSEY  MACOUPIN  MADISON  MONTGOMERY  \
0  184.46  188.865   186.265  ...  159.352632    164.56   153.92     167.555   
1  184.46  188.865   186.265  ...  159.352632    164.56   153.92     167.555   
2  184.46  188.865   186.265  ...  159.352632    164.56   153.92     167.555   
3  184.46  188.865   186.265  ...  159.352632    164.56   153.92     167.555   
4  184.46  188.865   186.265  ...  159.352632    164.56   153.92     167.555   

    MORGAN        PIKE  SANGAMON   SCOTT  OTHER (COMBINED) COUNTIES  \
0  182.115  159.431579   188.355  165.25                 153.015909   
1  182.115  159.431579   188.355  165.25                 153.015909   
2  182.115  159.431579   188.355  165.25                 153.015909   
3  182.115  159.431579   188.355  165.25                 153.015909   
4  182.115  159.431579   188.355  165.25                 153.015909   

   OTHER COUNTIES  
0           157.9  
1           157.9  
2           157.9  
3           157.9  
4           157.9  

[5 rows x 104 columns]

In [13]:
crev_guar75 = caph.mul(cbase)*.75
crev_guar75.head()

DE WITT       LOGAN       MACON    MARSHALL       MASON      MCLEAN  \
0  778.893667  550.470000  398.255288  738.861750  317.895237  749.371500   
1  569.086042  550.470000  561.497738  543.200213  498.322263  392.726175   
2  554.001833  546.341475  557.275950  777.173100  301.939105  641.128950   
3  543.031500  558.727050  561.497738  555.514575  697.160211  359.420775   
4  355.164542  781.667400  364.480987  528.149325  473.774368  641.128950   

       MENARD     PEORIA       STARK    TAZEWELL  ...      JERSEY  MACOUPIN  \
0  806.736441  639.15390  560.929050  579.749813  ...  482.838474  286.3344   
1  347.661794  536.77860  342.789975  395.347463  ...  552.156868  501.0852   
2  620.153471  534.01170  328.625100  542.031150  ...  463.716158  501.0852   
3  379.877559  547.84620  562.345538  839.589488  ...  277.273579  701.0256   
4  311.419059  549.22965  654.417225  754.373250  ...  338.225961  741.7542   

    MADISON  MONTGOMERY      MORGAN        PIKE    SANGAMON       SCOTT  \
0  326.6952  755.254163  336.002175  675.591316  347.514975  500.707500   
1  279.3648  678.597750  775.809900  294.151263  365.879588  478.398750   
2  445.5984  485.071725  775.809900  675.591316  559.414350  478.398750   
3  445.5984  510.204975  542.247413  718.637842  327.737700  669.262500   
4  267.8208  510.204975  544.979138  277.410947  573.540975  350.743125   

   OTHER (COMBINED) COUNTIES  OTHER COUNTIES  
0                 648.404915         459.489  
1                 459.047727         459.489  
2                 454.457250         459.489  
3                 651.847773         459.489  
4                 648.404915         459.489  

[5 rows x 104 columns]

# Beans:

In [14]:
#Linear Regression for beans
beanx = np.array(beans['Value']).reshape((-1,1))
beany = np.array(beans['Year']).reshape((-1,1))
beany.reshape((-1,1))
lr = LinearRegression()
regress = lr.fit(beany,beanx)
binter = regress.intercept_ #intercept
binter = binter[0]
bslope = regress.coef_ #slope
bslope = bslope[0]

In [15]:
beans = pd.merge(ci,beans)
aph = beans.groupby(['County'])['Value'].agg(['sum','count']).reset_index()
beans = pd.merge(aph,beans)
beans['Trend fitted yield'] = beans['Year']*bslope+binter
beans['Trend adjusted yield'] = beans['Value']+bslope*(2020-beans['Year'])
beans['Random Price'] = [round(random.uniform(8,17),2) for k in beans.index]
beans['Revenue'] = beans['Random Price']*beans['Trend adjusted yield']
beans['County APH'] = ((beans['sum'])/(beans['count']))

In [16]:
beans['bp guarantee'] = beans['County APH']*beans['Beans Base Price']
beans['hp guarantee'] = beans['County APH']*beans['Beans Harvest Price']
beans['Revenue Guarantee 75%'] = beans[['bp guarantee','hp guarantee']].max(axis = 1)*.75
beans['Revenue Guarantee 80%'] = beans[['bp guarantee','hp guarantee']].max(axis = 1)*.80
beans['Revenue Guarantee 85%'] = beans[['bp guarantee','hp guarantee']].max(axis = 1)*.85
beans['0'] = 0
beans['75% dif'] = beans['Revenue Guarantee 75%']-beans['Revenue']
beans['80% dif'] = beans['Revenue Guarantee 80%']-beans['Revenue']
beans['85% dif'] = beans['Revenue Guarantee 85%']-beans['Revenue']
beans['75% payout'] = beans[['75% dif','0']].max(axis = 1)
beans['80% payout'] = beans[['80% dif','0']].max(axis = 1)
beans['85% payout'] = beans[['85% dif','0']].max(axis = 1)
beans['75% Revenue'] = beans['75% payout']+beans['Revenue']
beans['80% Revenue'] = beans['80% payout']+beans['Revenue']
beans['85% Revenue'] = beans['85% payout']+beans['Revenue']
pd.set_option('display.max_columns', None)
beans

County     sum  count  Year  Corn Base Price  Corn Harvest Price  \
0        ADAMS   948.9     20  2001             2.46                2.05   
1        ADAMS   948.9     20  2002             2.32                2.52   
2        ADAMS   948.9     20  2003             2.42                2.37   
3        ADAMS   948.9     20  2004             2.83                1.99   
4        ADAMS   948.9     20  2005             2.32                1.93   
...        ...     ...    ...   ...              ...                 ...   
1972  WOODFORD  1118.5     20  2016             3.86                3.49   
1973  WOODFORD  1118.5     20  2017             3.97                3.49   
1974  WOODFORD  1118.5     20  2018             3.96                3.68   
1975  WOODFORD  1118.5     20  2019             4.00                3.90   
1976  WOODFORD  1118.5     20  2020             3.88                3.99   

      Beans Base Price  Beans Harvest Price Period     State  County ANSI  \
0                 4.67                 4.37   YEAR  ILLINOIS          1.0   
1                 4.50                 5.45   YEAR  ILLINOIS          1.0   
2                 5.26                 7.32   YEAR  ILLINOIS          1.0   
3                 6.72                 5.26   YEAR  ILLINOIS          1.0   
4                 5.53                 5.75   YEAR  ILLINOIS          1.0   
...                ...                  ...    ...       ...          ...   
1972              8.85                 9.75   YEAR  ILLINOIS        203.0   
1973             10.19                 9.75   YEAR  ILLINOIS        203.0   
1974             10.16                 8.60   YEAR  ILLINOIS        203.0   
1975              9.54                 9.25   YEAR  ILLINOIS        203.0   
1976              9.17                10.54   YEAR  ILLINOIS        203.0   

     Commodity                                Data Item  Value  CV (%)  \
0     SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   44.0     NaN   
1     SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   48.0     NaN   
2     SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   44.0     NaN   
3     SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   49.0     NaN   
4     SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   43.0     NaN   
...        ...                                      ...    ...     ...   
1972  SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   67.0     NaN   
1973  SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   60.4     NaN   
1974  SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   64.7     NaN   
1975  SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   61.4     NaN   
1976  SOYBEANS  SOYBEANS - YIELD, MEASURED IN BU / ACRE   62.2     2.3   

      Trend fitted yield  Trend adjusted yield  Random Price      Revenue  \
0              40.011797              61.91491         13.87   858.759798   
1              40.954687              64.97202          8.29   538.618044   
2              41.897577              60.02913         10.70   642.311689   
3              42.840467              64.08624         15.55   996.541029   
4              43.783357              57.14335         12.24   699.434602   
...                  ...                   ...           ...          ...   
1972           54.155147              70.77156         15.33  1084.928014   
1973           55.098037              63.22867         15.60   986.367251   
1974           56.040927              66.58578          9.36   623.242901   
1975           56.983817              62.34289         13.57   845.993017   
1976           57.926707              62.20000         16.14  1003.908000   

      County APH  bp guarantee  hp guarantee  Revenue Guarantee 75%  \
0         47.445     221.56815     207.33465             166.176112   
1         47.445     213.50250     258.57525             193.931437   
2         47.445     249.56070     347.29740             260.473050   
3         47.445     318.83040     249.56070             239.122800   
4

In [17]:
counties2 = beans.County.unique()
randomlist3 = []
randomlist4 = []
rand_yield_b = pd.DataFrame()
for n in counties2:
    for i in range(0,1000): #pulling random numbers for yield
        test = beans[beans['County'] == n]
        aph3 = test['County APH']
        b = list(aph3.astype(int))
        j = round(random.uniform(b[0]-20,b[0]+20),2)
        randomlist4.append(j)
    rand_yield_b[n] = randomlist4
    randomlist4.clear()

rand_yield_b.head()

ADAMS  ALEXANDER   BOND  BOONE  BROWN  BUREAU  CALHOUN  CARROLL   CASS  \
0  54.97      45.72  55.04  63.86  56.80   70.13    26.03    47.38  46.52   
1  55.56      52.92  46.56  68.96  51.37   73.87    39.66    38.02  59.69   
2  37.48      53.42  24.79  52.46  27.35   45.83    45.58    74.28  60.08   
3  52.49      56.67  44.94  62.18  54.33   64.63    45.38    67.18  53.19   
4  47.06      36.91  23.01  36.88  51.88   41.20    61.86    69.54  46.54   

   CHAMPAIGN  CHRISTIAN  CLARK   CLAY  CLINTON  COLES   COOK  CRAWFORD  \
0      73.94      36.68  52.78  44.98    31.30  74.88  25.46     41.24   
1      35.47      45.01  65.29  20.11    57.93  37.46  38.06     44.92   
2      37.22      73.18  40.07  51.25    27.72  52.85  48.73     37.59   
3      52.48      69.43  66.90  44.03    46.90  51.45  34.90     59.68   
4      67.28      67.38  37.40  31.78    59.91  39.24  47.24     31.69   

   CUMBERLAND  DE KALB  DE WITT  DOUGLAS  DU PAGE  EDGAR  EDWARDS  EFFINGHAM  \
0       47.76    41.33    73.63    53.10    35.64  70.50    57.08      64.78   
1       48.53    45.26    43.41    68.29    26.59  70.39    34.14      53.33   
2       63.63    69.56    51.03    67.65    24.39  70.99    27.46      48.33   
3       36.60    68.06    64.69    45.80    48.77  45.05    51.72      47.99   
4       56.92    60.14    46.55    45.17    39.08  44.81    40.57      37.98   

   FAYETTE   FORD  FRANKLIN  FULTON  GALLATIN  GREENE  GRUNDY  HAMILTON  \
0    42.12  33.68     30.56   37.82     55.16   64.61   40.66     36.03   
1    47.01  67.09     38.18   42.48     62.61   36.83   57.13     48.74   
2    30.61  57.30     55.45   48.66     59.58   52.74   41.98     20.97   
3    41.45  40.35     23.81   58.45     38.71   38.21   37.90     26.00   
4    36.52  59.16     27.43   43.00     39.92   42.91   44.65     50.12   

   HANCOCK  HARDIN  HENDERSON  HENRY  IROQUOIS  JACKSON  JASPER  JEFFERSON  \
0    34.61   19.42      56.15  33.03     68.55    54.80   54.52      34.63   
1    68.48   47.26      39.38  67.25     40.38    34.70   28.12      26.20   
2    56.02   46.42      56.33  59.96     68.43    27.46   37.56      43.83   
3    32.75   56.97      68.37  70.28     64.17    20.77   63.07      46.61   
4    61.35   52.47      43.05  60.91     61.22    33.16   46.13      35.27   

   JERSEY  JO DAVIESS  JOHNSON   KANE  KANKAKEE  KENDALL   KNOX  LA SALLE  \
0   35.19       58.11    43.34  48.21     62.43    57.52  71.68     55.42   
1   40.47       62.22    49.87  57.60     28.58    63.40  51.87     55.11   
2   53.75       59.46    34.86  36.48     47.64    51.59  62.41     64.83   
3   29.40       50.43    55.59  41.70     31.29    47.81  58.07     62.67   
4   60.57       61.92    49.04  59.50     33.98    52.33  61.79     65.25   

    LAKE  LAWRENCE    LEE  LIVINGSTON  LOGAN  MACON  MACOUPIN  MADISON  \
0  40.02     59.13  50.46       66.37  53.89  61.21     49.29    56.89   
1  21.50     62.76  55.13       56.86  45.25  49.32     64.21    50.08   
2  58.03     42.03  68.62       53.13  47.12  68.52     43.19    37.75   
3  28.09     35.84  68.28       66.85  60.39  59.47     50.33    65.69   
4  52.89     24.19  66.75       56.34  47.39  73.56     31.57    50.53   

   MARION  MARSHALL  MASON  MASSAC  MCDONOUGH  MCHENRY  MCLEAN  MENARD  \
0   44.65     62.87  53.74   41.72      39.51    65.64   46.13   51.18   
1   49.30     54.38  35.44   56.79      67.47    49.12   51.46   52.75   
2   46.40     54.54  49.50   51.27      34.36    46.59   66.07   35.85   
3   53.86     42.77  31.18   37.76      67.07    61.85   69.33   60.65   
4   58.30     60.54  48.01   26.43      40.07    63.82   62.95   47.35   

   MERCER  MONROE  MONTGOMERY  MORGAN  MOULTRIE   OGLE  \
0   42.66   59.09       50.22   44.85     74.23  60.93   
1   54.67   36.77       45.83   38.21     67.54  42.20   
2   66.78   47.87       53.96   61.84     56.16  61.76   
3   42.38   48.94       70.20   67.91     64.43  39.97   
4   34.81   35.22       35.94   39.96     63.83  48

In [18]:
rand_price_b = pd.DataFrame()
for n in counties2:
    for i in range(0,1000): #pulling random numbers for yield
        test = beans[beans['County'] == n]
        aph3 = test['Beans Base Price']
        sum = aph3.sum()
        b = list(aph3.astype(int))
        avg = sum/len(aph3)
        avg = avg.astype(int)
        j = round(random.uniform(avg-2,avg+2),2)
        randomlist4.append(j)
    rand_price_b[n] = randomlist4
    randomlist4.clear()

rand_price_b.head()

ADAMS  ALEXANDER  BOND  BOONE  BROWN  BUREAU  CALHOUN  CARROLL  CASS  \
0   8.83       7.83  8.92   8.07   9.19   10.81     8.49     9.22  9.96   
1   7.45       8.10  6.36   9.77   9.94   10.22     6.07     9.09  7.57   
2   8.74       8.92  8.14   7.78   8.95   10.53     6.89    10.11  8.40   
3   7.31       8.92  9.06   9.63   8.04    8.77     9.58     9.38  9.75   
4   7.58       8.70  6.77  10.46   9.51   10.22     9.28     7.20  9.31   

   CHAMPAIGN  CHRISTIAN  CLARK   CLAY  CLINTON  COLES  COOK  CRAWFORD  \
0      10.73       9.30   6.25   7.09    10.71  10.66  4.06      8.67   
1       7.16       7.26   7.29   8.25     9.93  10.76  5.50      8.63   
2       7.66       9.26   9.01  10.55     8.99   9.96  6.93      7.42   
3       9.70       7.31   8.80  10.03     9.10   8.28  5.83      7.46   
4       9.22       7.44   7.15   8.56     8.68   7.05  5.26      7.86   

   CUMBERLAND  DE KALB  DE WITT  DOUGLAS  DU PAGE  EDGAR  EDWARDS  EFFINGHAM  \
0        8.31     7.33     6.03     8.45     3.29   8.98     8.86       7.87   
1        9.18     8.01     8.28    10.15     4.51  10.52     6.05       7.85   
2        7.85    10.94     8.74    10.82     6.05   9.25     8.31       8.45   
3        8.79    10.16     6.76     7.24     6.32  10.20     8.10       9.28   
4        8.18     8.19     8.32     9.14     4.03   9.32     7.18       9.51   

   FAYETTE   FORD  FRANKLIN  FULTON  GALLATIN  GREENE  GRUNDY  HAMILTON  \
0    10.87   7.95      7.91    8.22      9.12    8.73    7.41      6.76   
1    10.70   9.86      9.93    8.17      8.73    7.57    7.12      9.31   
2     9.14   7.43      9.59    7.41     10.93    7.58    9.69      6.65   
3     7.73  10.36     10.86    7.23     10.89    8.98    9.36      9.09   
4     9.31   7.55      8.40    9.72     10.69    7.38   10.73      8.66   

   HANCOCK  HARDIN  HENDERSON  HENRY  IROQUOIS  JACKSON  JASPER  JEFFERSON  \
0     6.83    5.17       6.48   9.84      9.51     7.08    9.09      10.30   
1     9.34    8.14       6.34   7.84     10.18     6.65   10.47       8.95   
2     9.74    8.35       9.08   9.38      7.36     9.06    9.36      10.83   
3     7.11    5.39       8.97   9.18      9.91     6.33    9.77      10.23   
4     8.41    7.09       7.12   9.63      9.14     8.05    8.63       7.98   

   JERSEY  JO DAVIESS  JOHNSON   KANE  KANKAKEE  KENDALL  KNOX  LA SALLE  \
0    6.16        9.58     8.82   9.70     10.54     8.76  7.03      8.32   
1    9.54        9.59     7.20   7.11      8.66     8.58  7.70      9.40   
2    8.76        7.24     8.54   8.92     10.39     6.50  7.53      7.51   
3    8.78        7.03     6.23  10.51      8.74     9.04  9.38     10.44   
4    9.49        8.72     6.31   9.10      8.28     7.95  8.74      9.46   

   LAKE  LAWRENCE    LEE  LIVINGSTON  LOGAN  MACON  MACOUPIN  MADISON  MARION  \
0  7.93     10.50   9.64       10.91   7.63   8.81      9.49     7.68    7.76   
1  6.45      8.02   9.56        7.80   6.36   7.66      8.27     9.22    8.34   
2  6.01      7.82   7.61        8.47   8.68   7.66     10.43     8.64   10.05   
3  7.71     10.95   9.50        9.23   9.79   8.54      8.55     9.91    7.64   
4  7.24     10.18  10.53       10.18   8.94   7.86      9.69     9.41    8.87   

   MARSHALL  MASON  MASSAC  MCDONOUGH  MCHENRY  MCLEAN  MENARD  MERCER  \
0      9.77   8.20    9.26       9.66     9.11   10.06    6.20    7.75   
1      8.46   7.74    8.80       9.83     7.43   10.20    7.73    9.99   
2      7.08   7.38    6.71       7.03     8.87    7.52    6.00    8.25   
3      8.35   8.67    8.66       9.94     6.15    8.27    7.83    9.91   
4     10.28   6.41    6.27      10.27     7.52    8.73    6.30    9.29   

   MONROE  MONTGOMERY  MORGAN  MOULTRIE   OGLE  OTHER (COMBINED) COUNTIES  \
0    7.65        8.45    9.30      8.70   7.80                      11.20   
1    9.76        8.41    9.27      8.26  10.80                       9.90   
2    9.40        8.75    7.04      9.16  10.61                      11.67   
3    7.47      

In [19]:
randomlist6 = []
bbase = pd.DataFrame()
for n in counties:
    for i in range(0,1000): #pulling random numbers for yield
        test = beans[beans['County'] == n]
        aph3 = test['Beans Base Price']
        b = list(aph3)
        j = random.choices(b)
        randomlist6.append(j[0])
    bbase[n] = randomlist6
    randomlist6.clear()
bbase.head()

DE WITT  LOGAN  MACON  MARSHALL  MASON  MCLEAN  MENARD  PEORIA  STARK  \
0     8.85   8.85   9.73      9.17   9.54    8.09    9.73    8.80  12.87   
1     8.80   4.50   9.54     12.55  10.19    4.50   10.16   10.16   9.73   
2     9.17   6.72   8.85      9.17   5.26    9.54    8.85    8.80  12.55   
3     8.85   9.23   8.85      4.67   8.80    8.80    9.54    9.54   9.23   
4    10.19   4.50   8.85      9.54   4.67   10.16   12.55    9.54  11.36   

   TAZEWELL  WOODFORD  CHAMPAIGN   FORD  IROQUOIS  KANKAKEE  LIVINGSTON  \
0     12.87      9.23       6.72   8.09     10.16      9.54       13.49   
1     10.19      9.54       9.23  11.36      8.85     12.87       12.87   
2      5.26      9.17       9.73  11.36      8.80      5.53        9.54   
3      8.80      5.53       5.26   8.85     10.19      9.54        8.85   
4      6.72     12.87       9.17   9.17      9.23      5.53        9.54   

   PIATT  VERMILION  CLARK  CLAY  COLES  CRAWFORD  CUMBERLAND  DOUGLAS  EDGAR  \
0   9.17       8.09   8.09  6.72  11.36      5.26        9.23     5.53   8.85   
1  10.16       9.17   5.53  4.50   5.53     10.16       12.87     8.85  12.87   
2  11.36      13.36   9.17  5.53   8.80      9.54       13.49    12.87   4.50   
3   4.50       9.73   5.53  4.50   4.67     13.36        6.72    12.87   9.73   
4  13.36       8.09   8.80  8.85  11.36      9.73        8.85    13.36  10.19   

   EFFINGHAM  FAYETTE  JASPER  LAWRENCE  MARION  MOULTRIE  RICHLAND  SHELBY  \
0      12.55     9.17    9.73      9.73    5.53      6.72      8.85   12.55   
1      12.55     5.26   13.49      5.53    5.26      9.23      8.80    6.72   
2       4.50    11.36    4.50      8.80   13.49      6.18      4.50   12.55   
3       9.73    10.16    6.18     12.55   12.55      8.80      9.17   12.55   
4       6.72    13.49    9.23     12.55    8.80      9.23     11.36    9.54   

   BOONE  COOK  DE KALB  DU PAGE  GRUNDY   KANE  KENDALL  LA SALLE  LAKE  \
0  10.16  5.26     8.09     6.72    8.09  13.49    13.49      9.23  8.80   
1   9.73  6.72     5.53     5.26   10.19  13.36     8.80      4.67  4.50   
2  12.87  8.09     4.67     4.67   13.36   8.09     6.18      8.80  9.23   
3   9.23  5.26    10.16     5.26   12.87   4.50     5.53     13.36  9.73   
4   8.80  5.53     5.53     4.50    5.26   8.09    13.36     11.36  6.18   

   MCHENRY   WILL  BUREAU  CARROLL  HENRY  JO DAVIESS    LEE  MERCER   OGLE  \
0    13.36   5.26    5.26    11.36   8.85        9.73  12.87    8.80   9.73   
1     9.23   6.18   10.19     9.23  10.16       13.49  12.55    8.09   5.26   
2    12.87  13.49    6.18    10.16   5.26        9.73   4.50    9.54  12.55   
3    13.36   9.23    6.18    10.16  13.36        9.17   9.23    4.50   6.72   
4     8.80   5.26    9.54     6.18   5.53        8.80   8.85    9.23  13.36   

   PUTNAM  ROCK ISLAND  STEPHENSON  WHITESIDE  WINNEBAGO  EDWARDS  FRANKLIN  \
0   11.36         8.80        6.18       9.23       5.26    12.55     13.36   
1    9.73         8.80       10.16      10.16       4.50     6.72     10.16   
2    9.23         9.23        5.53      10.19       6.18    10.16     10.16   
3   12.55         4.50        8.09      10.16       6.18    13.49      8.85   
4   13.49         6.72       13.36       6.18       5.53    12.55      5.26   

   GALLATIN  HAMILTON  HARDIN  JEFFERSON  MASSAC  POPE  SALINE  WABASH  WAYNE  \
0      6.72      5.26    6.18      13.36    9.73  6.18   12.55    8.80   8.80   
1      4.50      9.23    8.09       4.67   12.87  9.23    8.80    4.50  12.55   
2     13.36     13.49    6.72       6.72    8.09  9.23    8.85   13.49   8.80   
3      6.72     10.16    6.18       6.72    9.23  9.73   10.19    6.72   4.67   
4      6.72     13.36    5.53      11.36    4.50  9.17   10.16    6.72   9.73   

   WHITE  ALEXANDER  CLINTON  JACKSON  JOHNSON  MONROE  PERRY  PULASKI  \
0   4.67       9.23    11.36    11.36     6.72    5.26  10.19     4.50   
1  11.36      10.19    10.16     9.54    13.36   12.55   8.09     9.54   
2   9.54       6.

In [20]:
randomlist6 = []
bharv = pd.DataFrame()
for n in counties:
    for i in range(0,1000): #pulling random numbers for yield
        test = beans[beans['County'] == n]
        aph3 = test['Beans Harvest Price']
        b = list(aph3)
        j = random.choices(b)
        randomlist6.append(j[0])
    bharv[n] = randomlist6
    randomlist6.clear()
bharv.head()

DE WITT  LOGAN  MACON  MARSHALL  MASON  MCLEAN  MENARD  PEORIA  STARK  \
0     9.75   9.75   9.25      9.22   9.22    5.45    9.65    5.93   5.45   
1     9.65   4.37   5.93      9.66  12.14    5.26    4.37    8.60   9.75   
2     9.65   5.75  11.63     15.39   9.75   12.87    9.22    5.75   8.91   
3     9.22   5.93   9.65      9.75   9.25    9.25    5.93    8.60   8.91   
4     9.75   8.91   9.25      9.22   9.75    5.75   15.39   12.14   8.91   

   TAZEWELL  WOODFORD  CHAMPAIGN  FORD  IROQUOIS  KANKAKEE  LIVINGSTON  PIATT  \
0      8.91      9.25      10.54  5.45     12.87      8.91        5.45  10.54   
1      8.91      9.22       4.37  5.93      9.22      8.91        7.32   5.75   
2      9.75      9.75       9.25  7.32      8.91      7.32        4.37   9.66   
3      4.37      4.37       9.75  7.32     10.54      9.75        9.75  15.39   
4     12.87      8.91      15.39  4.37      8.91      8.60       10.54   5.75   

   VERMILION  CLARK   CLAY  COLES  CRAWFORD  CUMBERLAND  DOUGLAS  EDGAR  \
0       5.93  10.54   4.37   9.75      5.75        9.66     8.91  11.63   
1       9.75   5.93   8.60   9.75     11.63        5.75    10.54   5.45   
2       9.65   7.32   8.60   8.60      9.75        4.37     9.75   7.32   
3       9.66   5.45   9.66   9.66      9.75        9.75     9.65  12.87   
4       9.65  10.54  12.14   9.75     12.87       15.39     8.91  12.87   

   EFFINGHAM  FAYETTE  JASPER  LAWRENCE  MARION  MOULTRIE  RICHLAND  SHELBY  \
0       8.60     5.45    5.75      5.93    9.66      9.22      8.60   12.14   
1       9.75     9.75   12.14     12.87    4.37     15.39     12.14   11.63   
2       5.26    12.87    9.25      9.75    8.60     12.87      5.45   15.39   
3       9.75     9.75    9.75      9.65    9.25      9.75      8.91   12.14   
4      15.39    10.54    9.65     12.14   10.54      9.75      4.37    8.60   

   BOONE  COOK  DE KALB  DU PAGE  GRUNDY   KANE  KENDALL  LA SALLE   LAKE  \
0   5.93  5.45     9.22     5.93    9.66   4.37    12.14     12.87   9.65   
1   9.66  9.75     8.60     9.75   12.14  12.87     5.93     12.87   8.60   
2   9.75  4.37     5.45     5.45    9.66   9.25    12.14      9.75  15.39   
3   9.75  7.32     4.37     5.45    9.66   9.65     5.93      9.75   9.75   
4   5.93  5.45     9.65     5.26    9.75  12.87     5.75     15.39  15.39   

   MCHENRY  WILL  BUREAU  CARROLL  HENRY  JO DAVIESS    LEE  MERCER   OGLE  \
0     5.93  9.75    9.65     9.75   9.65        9.75   5.75    9.75  11.63   
1     9.75  7.32    8.91     4.37   4.37        5.75   9.66    7.32  12.87   
2     8.60  9.75    5.75     4.37   5.45        9.66  12.14   10.54   5.93   
3    12.87  5.26   12.14     9.75   7.32        9.65   5.93   12.14   5.26   
4     5.75  5.93    5.93     5.93  10.54        9.22  12.87    9.65   5.26   

   PUTNAM  ROCK ISLAND  STEPHENSON  WHITESIDE  WINNEBAGO  EDWARDS  FRANKLIN  \
0    9.22         9.22        9.75       9.75       9.22    12.87      8.91   
1    9.75        12.14        9.65       9.22      12.87     9.75      9.25   
2    9.75         4.37       15.39       9.66       9.65     9.75      9.75   
3   15.39         5.75       10.54       9.66       9.75     9.65      5.75   
4    9.75         5.45        9.65       8.91       7.32     9.75      8.91   

   GALLATIN  HAMILTON  HARDIN  JEFFERSON  MASSAC  POPE  SALINE  WABASH  WAYNE  \
0      9.66      9.22    4.37       9.25    9.66  9.75   15.39    5.93   9.22   
1      5.93      9.75    5.26      12.14   10.54  7.32    9.75    9.22  10.54   
2      5.45      8.60    8.91       9.25    5.26  9.75    8.60    9.65   9.25   
3      9.75      9.75    8.60       9.25   12.14  5.93    5.93    9.75   9.25   
4     11.63      9.75    5.75       9.65    5.26  8.91   10.54   12.87   4.37   

   WHITE  ALEXANDER  CLINTON  JACKSON  JOHNSON  MONROE  PERRY  PULASKI  \
0   9.25       9.75    11.63     9.75     9.22    5.93  12.14     4.37   
1   5.26       9.75     5.93    11.63     8.91   15.39   7.32     8.60   
2  12.87       5.

In [21]:
bmax = bbase.where(bbase > bharv).fillna(bharv)
bmax.head()

DE WITT  LOGAN  MACON  MARSHALL  MASON  MCLEAN  MENARD  PEORIA  STARK  \
0     9.75   9.75   9.73      9.22   9.54    8.09    9.73    8.80  12.87   
1     9.65   4.50   9.54     12.55  12.14    5.26   10.16   10.16   9.75   
2     9.65   6.72  11.63     15.39   9.75   12.87    9.22    8.80  12.55   
3     9.22   9.23   9.65      9.75   9.25    9.25    9.54    9.54   9.23   
4    10.19   8.91   9.25      9.54   9.75   10.16   15.39   12.14  11.36   

   TAZEWELL  WOODFORD  CHAMPAIGN   FORD  IROQUOIS  KANKAKEE  LIVINGSTON  \
0     12.87      9.25      10.54   8.09     12.87      9.54       13.49   
1     10.19      9.54       9.23  11.36      9.22     12.87       12.87   
2      9.75      9.75       9.73  11.36      8.91      7.32        9.54   
3      8.80      5.53       9.75   8.85     10.54      9.75        9.75   
4     12.87     12.87      15.39   9.17      9.23      8.60       10.54   

   PIATT  VERMILION  CLARK   CLAY  COLES  CRAWFORD  CUMBERLAND  DOUGLAS  \
0  10.54       8.09  10.54   6.72  11.36      5.75        9.66     8.91   
1  10.16       9.75   5.93   8.60   9.75     11.63       12.87    10.54   
2  11.36      13.36   9.17   8.60   8.80      9.75       13.49    12.87   
3  15.39       9.73   5.53   9.66   9.66     13.36        9.75    12.87   
4  13.36       9.65  10.54  12.14  11.36     12.87       15.39    13.36   

   EDGAR  EFFINGHAM  FAYETTE  JASPER  LAWRENCE  MARION  MOULTRIE  RICHLAND  \
0  11.63      12.55     9.17    9.73      9.73    9.66      9.22      8.85   
1  12.87      12.55     9.75   13.49     12.87    5.26     15.39     12.14   
2   7.32       5.26    12.87    9.25      9.75   13.49     12.87      5.45   
3  12.87       9.75    10.16    9.75     12.55   12.55      9.75      9.17   
4  12.87      15.39    13.49    9.65     12.55   10.54      9.75     11.36   

   SHELBY  BOONE  COOK  DE KALB  DU PAGE  GRUNDY   KANE  KENDALL  LA SALLE  \
0   12.55  10.16  5.45     9.22     6.72    9.66  13.49    13.49     12.87   
1   11.63   9.73  9.75     8.60     9.75   12.14  13.36     8.80     12.87   
2   15.39  12.87  8.09     5.45     5.45   13.36   9.25    12.14      9.75   
3   12.55   9.75  7.32    10.16     5.45   12.87   9.65     5.93     13.36   
4    9.54   8.80  5.53     9.65     5.26    9.75  12.87    13.36     15.39   

    LAKE  MCHENRY   WILL  BUREAU  CARROLL  HENRY  JO DAVIESS    LEE  MERCER  \
0   9.65    13.36   9.75    9.65    11.36   9.65        9.75  12.87    9.75   
1   8.60     9.75   7.32   10.19     9.23  10.16       13.49  12.55    8.09   
2  15.39    12.87  13.49    6.18    10.16   5.45        9.73  12.14   10.54   
3   9.75    13.36   9.23   12.14    10.16  13.36        9.65   9.23   12.14   
4  15.39     8.80   5.93    9.54     6.18  10.54        9.22  12.87    9.65   

    OGLE  PUTNAM  ROCK ISLAND  STEPHENSON  WHITESIDE  WINNEBAGO  EDWARDS  \
0  11.63   11.36         9.22        9.75       9.75       9.22    12.87   
1  12.87    9.75        12.14       10.16      10.16      12.87     9.75   
2  12.55    9.75         9.23       15.39      10.19       9.65    10.16   
3   6.72   15.39         5.75       10.54      10.16       9.75    13.49   
4  13.36   13.49         6.72       13.36       8.91       7.32    12.55   

   FRANKLIN  GALLATIN  HAMILTON  HARDIN  JEFFERSON  MASSAC  POPE  SALINE  \
0     13.36      9.66      9.22    6.18      13.36    9.73  9.75   15.39   
1     10.16      5.93      9.75    8.09      12.14   12.87  9.23    9.75   
2     10.16     13.36     13.49    8.91       9.25    8.09  9.75    8.85   
3      8.85      9.75     10.16    8.60       9.25   12.14  9.73   10.19   
4      8.91     11.63     13.36    5.75      11.36    5.26  9.17   10.54   

   WABASH  WAYNE  WHITE  ALEXANDER  CLINTON  JACKSON  JOHNSON  MONROE  PERRY  \
0    8.80   9.22   9.25       9.75    11.63    11.36     9.22    5.93  12.14   
1    9.22  12.55  11.36      10.19    10.16    11.63    13.36   15.39   8.09   
2   13.49   9.25  12.87       6.72    12.55     5.53    12.14    8.09  12.14 

In [22]:
randomlist5 = []
baph = pd.DataFrame()
for n in counties:
    for i in range(0,1000): #pulling random numbers for yield
        test = beans[beans['County'] == n]
        aph3 = test['County APH']
        b = list(aph3)
        j = b[0]
        randomlist5.append(j)
    baph[n] = randomlist5
    randomlist5.clear()
baph.head()

DE WITT      LOGAN   MACON  MARSHALL      MASON  MCLEAN     MENARD  \
0  57.138889  55.742105  57.285    53.225  48.457895   56.71  53.789474   
1  57.138889  55.742105  57.285    53.225  48.457895   56.71  53.789474   
2  57.138889  55.742105  57.285    53.225  48.457895   56.71  53.789474   
3  57.138889  55.742105  57.285    53.225  48.457895   56.71  53.789474   
4  57.138889  55.742105  57.285    53.225  48.457895   56.71  53.789474   

   PEORIA      STARK  TAZEWELL  WOODFORD  CHAMPAIGN   FORD  IROQUOIS  \
0  53.795  54.889474     56.72    55.925      55.75  50.93     50.05   
1  53.795  54.889474     56.72    55.925      55.75  50.93     50.05   
2  53.795  54.889474     56.72    55.925      55.75  50.93     50.05   
3  53.795  54.889474     56.72    55.925      55.75  50.93     50.05   
4  53.795  54.889474     56.72    55.925      55.75  50.93     50.05   

   KANKAKEE  LIVINGSTON      PIATT  VERMILION      CLARK   CLAY   COLES  \
0     47.78       51.99  59.257895  54.715789  49.266667  40.15  55.425   
1     47.78       51.99  59.257895  54.715789  49.266667  40.15  55.425   
2     47.78       51.99  59.257895  54.715789  49.266667  40.15  55.425   
3     47.78       51.99  59.257895  54.715789  49.266667  40.15  55.425   
4     47.78       51.99  59.257895  54.715789  49.266667  40.15  55.425   

   CRAWFORD  CUMBERLAND  DOUGLAS  EDGAR  EFFINGHAM  FAYETTE  JASPER  \
0     45.98       49.59    56.98  54.63     48.065   44.035  46.865   
1     45.98       49.59    56.98  54.63     48.065   44.035  46.865   
2     45.98       49.59    56.98  54.63     48.065   44.035  46.865   
3     45.98       49.59    56.98  54.63     48.065   44.035  46.865   
4     45.98       49.59    56.98  54.63     48.065   44.035  46.865   

    LAWRENCE  MARION  MOULTRIE   RICHLAND  SHELBY  BOONE       COOK  DE KALB  \
0  44.184211  42.215    57.005  41.489474  51.185  49.08  39.428571    53.34   
1  44.184211  42.215    57.005  41.489474  51.185  49.08  39.428571    53.34   
2  44.184211  42.215    57.005  41.489474  51.185  49.08  39.428571    53.34   
3  44.184211  42.215    57.005  41.489474  51.185  49.08  39.428571    53.34   
4  44.184211  42.215    57.005  41.489474  51.185  49.08  39.428571    53.34   

     DU PAGE  GRUNDY    KANE    KENDALL  LA SALLE       LAKE    MCHENRY  \
0  39.571429   49.75  50.575  49.417647     52.69  39.435294  46.731579   
1  39.571429   49.75  50.575  49.417647     52.69  39.435294  46.731579   
2  39.571429   49.75  50.575  49.417647     52.69  39.435294  46.731579   
3  39.571429   49.75  50.575  49.417647     52.69  39.435294  46.731579   
4  39.571429   49.75  50.575  49.417647     52.69  39.435294  46.731579   

     WILL  BUREAU  CARROLL  HENRY  JO DAVIESS   LEE  MERCER   OGLE     PUTNAM  \
0  47.805   54.42    58.52  53.31   51.010526  53.0  52.695  52.73  52.888889   
1  47.805   54.42    58.52  53.31   51.010526  53.0  52.695  52.73  52.888889   
2  47.805   54.42    58.52  53.31   51.010526  53.0  52.695  52.73  52.888889   
3  47.805   54.42    58.52  53.31   51.010526  53.0  52.695  52.73  52.888889   
4  47.805   54.42    58.52  53.31   51.010526  53.0  52.695  52.73  52.888889   

   ROCK ISLAND  STEPHENSON  WHITESIDE  WINNEBAGO    EDWARDS  FRANKLIN  \
0    51.952632       53.04  52.077778     47.685  42.761111     38.77   
1    51.952632       53.04  52.077778     47.685  42.761111     38.77   
2    51.952632       53.04  52.077778     47.685  42.761111     38.77   
3    51.952632       53.04  52.077778     47.685  42.761111     38.77   
4    51.952632       53.04  52.077778     47.685  42.761111     38.77   

   GALLATIN   HAMILTON     HARDIN  JEFFERSON  MASSAC       POPE     SALINE  \
0    44.435  39.944444  37.792308     37.255    39.7  35.783333  42.005556   
1    44.435  39.944444  37.792308     37.255    39.7  35.783333  42.005556   
2    44.435  39.944444  37.792308     37.255    39.7  35.783333  42.005556   
3    44.435  39.944444  37.792308     37.255    39.7  35.783333  42.00555

In [23]:
brev = rand_price_b.mul(rand_yield_b)
brev.head()

ADAMS  ALEXANDER      BOND     BOONE     BROWN    BUREAU   CALHOUN  \
0  485.3851   357.9876  490.9568  515.3502  521.9920  758.1053  220.9947   
1  413.9220   428.6520  296.1216  673.7392  510.6178  754.9514  240.7362   
2  327.5752   476.5064  201.7906  408.1388  244.7825  482.5899  314.0462   
3  383.7019   505.4964  407.1564  598.7934  436.8132  566.8051  434.7404   
4  356.7148   321.1170  155.7777  385.7648  493.3788  421.0640  574.0608   

    CARROLL      CASS  CHAMPAIGN  CHRISTIAN     CLARK      CLAY   CLINTON  \
0  436.8436  463.3392   793.3762   341.1240  329.8750  318.9082  335.2230   
1  345.6018  451.8533   253.9652   326.7726  475.9641  165.9075  575.2449   
2  750.9708  504.6720   285.1052   677.6468  361.0307  540.6875  249.2028   
3  630.1484  518.6025   509.0560   507.5333  588.7200  441.6209  426.7900   
4  500.6880  433.2874   620.3216   501.3072  267.4100  272.0368  520.0188   

      COLES      COOK  CRAWFORD  CUMBERLAND   DE KALB   DE WITT   DOUGLAS  \
0  798.2208  103.3676  357.5508    396.8856  302.9489  443.9889  448.6950   
1  403.0696  209.3300  387.6596    445.5054  362.5326  359.4348  693.1435   
2  526.3860  337.6989  278.9178    499.4955  760.9864  446.0022  731.9730   
3  426.0060  203.4670  445.2128    321.7140  691.4896  437.3044  331.5920   
4  276.6420  248.4824  249.0834    465.6056  492.5466  387.2960  412.8538   

    DU PAGE     EDGAR   EDWARDS  EFFINGHAM   FAYETTE      FORD  FRANKLIN  \
0  117.2556  633.0900  505.7288   509.8186  457.8444  267.7560  241.7296   
1  119.9209  740.5028  206.5470   418.6405  503.0070  661.5074  379.1274   
2  147.5595  656.6575  228.1926   408.3885  279.7754  425.7390  531.7655   
3  308.2264  459.5100  418.9320   445.3472  320.4085  418.0260  258.5766   
4  157.4924  417.6292  291.2926   361.1898  340.0012  446.6580  230.4120   

     FULTON  GALLATIN    GREENE    GRUNDY  HAMILTON   HANCOCK    HARDIN  \
0  310.8804  503.0592  564.0453  301.2906  243.5628  236.3863  100.4014   
1  347.0616  546.5853  278.8031  406.7656  453.7694  639.6032  384.6964   
2  360.5706  651.2094  399.7692  406.7862  139.4505  545.6348  387.6070   
3  422.5935  421.5519  343.1258  354.7440  236.3400  232.8525  307.0683   
4  417.9600  426.7448  316.6758  479.0945  434.0392  515.9535  372.0123   

   HENDERSON     HENRY  IROQUOIS   JACKSON    JASPER  JEFFERSON    JERSEY  \
0   363.8520  325.0152  651.9105  387.9840  495.5868   356.6890  216.7704   
1   249.6692  527.2400  411.0684  230.7550  294.4164   234.4900  386.0838   
2   511.4764  562.4248  503.6448  248.7876  351.5616   474.6789  470.8500   
3   613.2789  645.1704  635.9247  131.4741  616.1939   476.8203  258.1320   
4   306.5160  586.5633  559.5508  266.9380  398.1019   281.4546  574.8093   

   JO DAVIESS   JOHNSON      KANE  KANKAKEE   KENDALL      KNOX  LA SALLE  \
0    556.6938  382.2588  467.6370  658.0122  503.8752  503.9104  461.0944   
1    596.6898  359.0640  409.5360  247.5028  543.9720  399.3990  518.0340   
2    430.4904  297.7044  325.4016  494.9796  335.3350  469.9473  486.8733   
3    354.5229  346.3257  438.2670  273.4746  432.2024  544.6966  654.2748   
4    539.9424  309.4424  541.4500  281.3544  416.0235  540.0446  617.2650   

       LAKE  LAWRENCE       LEE  LIVINGSTON     LOGAN     MACON  MACOUPIN  \
0  317.3586  620.8650  486.4344    724.0967  411.1807  539.2601  467.7621   
1  138.6750  503.3352  527.0428    443.5080  287.7900  377.7912  531.0167   
2  348.7603  328.6746  522.1982    450.0111  409.0016  524.8632  450.4717   
3  216.5739  392.4480  648.6600    617.0255  591.2181  507.8738  430.3215   
4  382.9236  246.2542  702.8775    573.5412  423.6666  578.1816  305.9133   

    MADISON    MARION  MARSHALL     MASON    MASSAC  MCDONOUGH   MCHENRY  \
0  436.9152  346.4840  614.2399  440.6680  386.3272   381.6666  597.9804   
1  461.7376  411.1620  460.0548  274.3056  499.7520   663.2301  364.9616   
2  326.1600  466.3200  386.1432  365.3100  344.0217   241.5508  413.2533   
3  650.9879  411.4904 

In [24]:
brev_guar75 = baph.mul(bmax)*.75
brev_guar75.head()

DE WITT       LOGAN       MACON    MARSHALL       MASON      MCLEAN  \
0  417.828125  407.614145  418.037288  368.050875  346.716237  344.087925   
1  413.542708  188.129605  409.874175  500.980313  441.209132  223.720950   
2  413.542708  280.940211  499.668413  614.349563  354.348355  547.393275   
3  395.115417  385.874724  414.600188  389.207813  336.176645  393.425625   
4  436.683958  372.496618  397.414688  380.824875  354.348355  432.130200   

       MENARD      PEORIA       STARK  TAZEWELL    WOODFORD   CHAMPAIGN  \
0  392.528684  355.047000  529.820645  547.4898  387.979687  440.703750   
1  409.875789  409.917900  401.379276  433.4826  400.143375  385.929375   
2  371.954211  355.047000  516.647171  414.7650  408.951562  406.835625   
3  384.863684  384.903225  379.972382  374.3520  231.948937  407.671875   
4  620.865000  489.803475  467.658316  547.4898  539.816062  643.494375   

         FORD    IROQUOIS   KANKAKEE  LIVINGSTON       PIATT   VERMILION  \
0  309.017775  483.107625  341.86590  526.008825  468.433658  331.988053   
1  433.923600  346.095750  461.19645  501.833475  451.545158  400.109211   
2  433.923600  334.459125  262.31220  371.988450  504.877263  548.252211   
3  338.047875  395.645250  349.39125  380.176875  683.984250  399.288474   
4  350.271075  346.471125  308.18100  410.980950  593.764105  396.005526   

      CLARK       CLAY       COLES   CRAWFORD  CUMBERLAND    DOUGLAS  \
0  389.4530  202.35600  472.221000  198.28875  359.279550  380.76885   
1  219.1135  258.96750  405.295312  401.06055  478.667475  450.42690   
2  338.8315  258.96750  365.805000  336.22875  501.726825  549.99945   
3  204.3335  290.88675  401.554125  460.71960  362.626875  549.99945   
4  389.4530  365.56575  472.221000  443.82195  572.392575  570.93960   

        EDGAR   EFFINGHAM     FAYETTE      JASPER    LAWRENCE      MARION  \
0  476.510175  452.411812  302.850712  341.997338  322.434276  305.847675   
1  527.316075  452.411812  322.005937  474.156637  426.488092  166.538175   
2  299.918700  189.616425  425.047837  325.125938  323.097039  427.110262   
3  527.316075  351.475312  335.546700  342.700312  415.883882  397.348687   
4  527.316075  554.790262  445.524113  339.185438  415.883882  333.709575   

     MOULTRIE    RICHLAND      SHELBY     BOONE        COOK    DE KALB  \
0  394.189575  275.386382  481.778813  373.9896  161.164286  368.84610   
1  657.980212  377.761658  446.461163  358.1613  288.321429  344.04300   
2  550.240762  169.588224  590.802862  473.7447  239.232857  218.02725   
3  416.849062  285.343855  481.778813  358.8975  216.462857  406.45080   
4  416.849062  353.490316  366.228675  323.9280  163.530000  386.04825   

      DU PAGE      GRUNDY        KANE     KENDALL    LA SALLE        LAKE  \
0  199.440000  360.438750  511.692562  499.983044  508.590225  285.412941   
1  289.366071  452.973750  506.761500  326.156471  508.590225  254.357647   
2  161.748214  498.495000  350.864062  449.947676  385.295625  455.181882   
3  161.748214  480.211875  366.036563  219.784985  527.953800  288.370588   
4  156.109286  363.796875  488.175187  495.164824  608.174325  455.181882   

      MCHENRY        WILL     BUREAU   CARROLL       HENRY  JO DAVIESS  \
0  468.250421  349.574062  393.86475  498.5904  385.831125  373.014474   
1  341.724671  262.449450  415.90485  405.1047  406.222200  516.099000   
2  451.076566  483.667087  252.23670  445.9224  217.904625  372.249316   
3  468.250421  330.930112  495.49410  445.9224  534.166200  369.188684   
4  308.428421  212.612737  389.37510  271.2402  421.415550  352.737789   

        LEE      MERCER        OGLE      PUTNAM  ROCK ISLAND  STEPHENSON  \
0  511.5825  385.332187  459.937425  450.613333   359.252447    387.8550   
1  498.8625  319.726912  508.976325  386.750000   473.028711    404.1648   
2  482.5650  416.553975  496.321125  386.750000   359.642092    612.2142   
3  366.8925  479.787975  265.759200  610.470000   224.045724    419.2812   
4  511

In [25]:
bdif75 = brev_guar75-brev
bdif75

ADAMS   ALEXANDER        BOND     BOONE       BROWN     BUREAU  \
0    -38.809038  -68.308136 -211.205967 -141.3606  -94.284625 -364.24055   
1    -85.483988 -125.899821  142.696858 -315.5779 -200.582800 -339.04655   
2    152.449587 -276.850400  112.115858   65.6059  164.956938 -230.35320   
3     62.874162 -215.816936  -89.997025 -239.8959    5.338988  -71.31100   
4     75.271925   79.680536  278.811967  -61.8368 -179.468363  -31.68890   
..          ...         ...         ...       ...         ...        ...   
995   83.548162   42.272850 -124.227942 -149.3883   36.678375 -172.86405   
996 -220.389800   81.521893 -126.167667    4.1021   67.282762 -351.09540   
997   95.643862  -27.356414 -134.564550  -72.2406 -102.180813   62.47125   
998 -179.602475 -130.593607 -114.246958 -258.0734 -193.197000   30.80340   
999 -157.447613  -28.470836  227.445467  -14.5223  -38.676500   71.07905   

        CALHOUN   CARROLL        CASS   CHAMPAIGN   CHRISTIAN     CLARK  \
0    314.513175   61.7468  -62.550411 -352.672450  -31.545789   59.5780   
1     80.081383   59.5029  -69.157037  131.964175   85.575426 -256.8506   
2     81.234467 -305.0484 -297.787895  121.730425 -107.126300  -22.1992   
3     30.131933 -184.2260 -118.993658 -101.384125   36.766095 -384.3865   
4   -235.497342 -229.4478   60.323916   23.172775 -111.373989  122.0430   
..          ...       ...         ...         ...         ...       ...   
995 -201.321942 -386.3673 -169.394858   81.241375  200.167758  -12.8070   
996   15.664467 -130.7241 -136.104037 -383.399325  -36.007311   -8.8232   
997   29.880083  -20.7867 -150.213126 -482.007250  197.237121 -141.7043   
998 -143.574858 -134.3483  133.532763  -83.428125  -45.455053  -86.7949   
999  196.907533 -187.2229  -51.426126 -168.728475 -230.226047  211.5275   

          CLAY   CLINTON       COLES        COOK   CRAWFORD  CUMBERLAND  \
0   -116.55220   42.9846 -325.999800   57.796686 -159.26205  -37.606050   
1     93.06000 -244.8417    2.225712   78.991429   13.40095   33.162075   
2   -281.72000  158.9232 -160.581000  -98.466043   57.31095    2.231325   
3   -150.73415 -109.7200  -24.451875   12.995857   15.50680   40.912875   
4     93.52895  -85.5516  195.579000  -84.952400  194.73855  106.786975   
..         ...       ...         ...         ...        ...         ...   
995   74.54885 -186.3700 -160.761300   37.582686  -75.47640  157.806075   
996 -108.74400   24.5430  138.215437  -17.316000   11.30435  153.337725   
997 -167.93040   34.3100 -179.548375   87.555857  231.58970  168.993075   
998  -19.05750  -67.4216 -130.455375 -161.326786  -85.98735 -330.382025   
999  -78.74485  -39.6200 -133.179375  -51.650571 -124.23745  118.855200   

       DE KALB     DE WITT    DOUGLAS     DU PAGE       EDGAR     EDWARDS  \
0     65.89720  -26.160775  -67.92615   82.184400 -156.579825  -92.977175   
1    -18.48960   54.107908 -242.71660  169.445171 -213.186725  106.143625   
2   -542.95915  -32.459492 -181.97355   14.188714 -356.738800   97.647067   
3   -285.03880  -42.188983  218.40745 -146.478186   67.806075   13.703542   
4   -106.49835   49.387958  158.08580   -1.383114  109.686875  111.196358   
..         ...         ...        ...         ...         ...         ...   
995  193.49135 -194.151875   41.81205   -3.598786 -247.310250 -123.816133   
996 -183.02565 -183.309250  262.12175 -117.165286   49.726650   86.472167   
997 -207.46590 -157.788675   81.53405   30.571286 -176.077425  -38.894933   
998  139.30860    9.614525   43.65000    0.975429  -42.180475    1.647125   
999  -63.94005  -83.087150  -14.89830   34.182214  -40.370525   49.784600   

      EFFINGHAM     FAYETTE        FORD    FRANKLIN    FULTON    GALLATIN  \
0    -57.406788 -154.993687   41.261775  146.745800   56.2071 -181.127625   
1     33.771313 -181.001062 -227.583800  -83.700000  -71.4636 -348.960638   
2   -218.772075  145.272437    8.184600 -236.338100  218.8629 -205.970700   
3    -93.871888   15.138200  -79.978125   -1.240725 -118.0050 

In [26]:
bpay75 = bdif75.where(bdif75 > 0).fillna(0)
bpay75.head()

ADAMS  ALEXANDER        BOND    BOONE       BROWN  BUREAU     CALHOUN  \
0    0.000000   0.000000    0.000000   0.0000    0.000000     0.0  314.513175   
1    0.000000   0.000000  142.696858   0.0000    0.000000     0.0   80.081383   
2  152.449587   0.000000  112.115858  65.6059  164.956938     0.0   81.234467   
3   62.874162   0.000000    0.000000   0.0000    5.338988     0.0   30.131933   
4   75.271925  79.680536  278.811967   0.0000    0.000000     0.0    0.000000   

   CARROLL       CASS   CHAMPAIGN  CHRISTIAN    CLARK      CLAY   CLINTON  \
0  61.7468   0.000000    0.000000   0.000000   59.578   0.00000   42.9846   
1  59.5029   0.000000  131.964175  85.575426    0.000  93.06000    0.0000   
2   0.0000   0.000000  121.730425   0.000000    0.000   0.00000  158.9232   
3   0.0000   0.000000    0.000000  36.766095    0.000   0.00000    0.0000   
4   0.0000  60.323916   23.172775   0.000000  122.043  93.52895    0.0000   

        COLES       COOK   CRAWFORD  CUMBERLAND  DE KALB    DE WITT  \
0    0.000000  57.796686    0.00000    0.000000  65.8972   0.000000   
1    2.225712  78.991429   13.40095   33.162075   0.0000  54.107908   
2    0.000000   0.000000   57.31095    2.231325   0.0000   0.000000   
3    0.000000  12.995857   15.50680   40.912875   0.0000   0.000000   
4  195.579000   0.000000  194.73855  106.786975   0.0000  49.387958   

     DOUGLAS     DU PAGE       EDGAR     EDWARDS   EFFINGHAM     FAYETTE  \
0    0.00000   82.184400    0.000000    0.000000    0.000000    0.000000   
1    0.00000  169.445171    0.000000  106.143625   33.771313    0.000000   
2    0.00000   14.188714    0.000000   97.647067    0.000000  145.272437   
3  218.40745    0.000000   67.806075   13.703542    0.000000   15.138200   
4  158.08580    0.000000  109.686875  111.196358  193.600462  105.522912   

        FORD    FRANKLIN    FULTON  GALLATIN      GREENE      GRUNDY  \
0  41.261775  146.745800   56.2071       0.0    0.000000   59.148150   
1   0.000000    0.000000    0.0000       0.0  119.951500   46.208150   
2   8.184600    0.000000  218.8629       0.0   76.695450   91.708800   
3   0.000000    0.000000    0.0000       0.0    6.569425  125.467875   
4   0.000000   28.668525    0.0000       0.0  188.439525    0.000000   

     HAMILTON     HANCOCK     HARDIN  HENDERSON      HENRY  IROQUOIS  \
0   32.653033  143.429371  74.765946   165.7725  60.815925       0.0   
1    0.000000    0.000000   0.000000   279.9553   0.000000       0.0   
2  264.687417    0.000000   0.000000     0.0000   0.000000       0.0   
3   68.036667  288.662132   0.000000     0.0000   0.000000       0.0   
4    0.000000    0.000000   0.000000   297.7035   0.000000       0.0   

      JACKSON      JASPER   JEFFERSON      JERSEY  JO DAVIESS  JOHNSON  \
0    0.000000    0.000000   16.606100  138.425258    0.000000   0.0000   
1  125.316833  179.740237  104.716775   31.620411    0.000000  33.4528   
2    0.000000    0.000000    0.000000    0.000000    0.000000  58.9688   
3  160.608900    0.000000    0.000000  100.372934   14.665784   0.0000   
4    0.000000    0.000000   35.958000    0.000000    0.000000  24.3144   

        KANE   KANKAKEE     KENDALL        KNOX   LA SALLE        LAKE  \
0  44.055562    0.00000    0.000000    0.000000  47.495825    0.000000   
1  97.225500  213.69365    0.000000  158.378775   0.000000  115.682647   
2  25.462463    0.00000  114.612676    0.000000   0.000000  106.421582   
3   0.000000   75.91665    0.000000    0.000000   0.000000   71.796688   
4   0.000000   26.82660   79.141324    0.000000   0.000000   72.258282   

     LAWRENCE      LEE  LIVINGSTON  LOGAN      MACON    MACOUPIN  MADISON  \
0    0.000000  25.1481    0.000000    0.0   0.000000    0.000000      0.0   
1    0.000000   0.0000   58.325475    0.0  32.082975    0.000000      0.0   
2    0.000000   0.0000    0.000000    0.0   0.000000  139.638613      0.0   
3   23.435882   0.0000    0.000000    0.0   0.000000    0.000000      0.0   
4  169.629682   0.0000    0.00000

In [27]:
brev75 = bpay75+brev
brev75

ADAMS   ALEXANDER        BOND     BOONE       BROWN     BUREAU  \
0    485.385100  357.987600  490.956800  515.3502  521.992000  758.10530   
1    413.922000  428.652000  438.818458  673.7392  510.617800  754.95140   
2    480.024787  476.506400  313.906458  473.7447  409.739438  482.58990   
3    446.576062  505.496400  407.156400  598.7934  442.152187  566.80510   
4    431.986725  400.797536  434.589667  385.7648  493.378800  421.06400   
..          ...         ...         ...       ...         ...        ...   
995  457.962862  272.447250  422.520400  645.9552  340.333875  698.15310   
996  695.788700  274.229893  405.918500  218.2833  339.981562  625.37220   
997  457.962862  301.289200  444.892800  341.6898  555.607000  512.22825   
998  611.589200  404.823500  522.488000  451.6940  593.424000  545.28840   
999  472.363800  318.150300  434.589667  488.2670  509.366000  397.94625   

        CALHOUN   CARROLL        CASS   CHAMPAIGN   CHRISTIAN     CLARK  \
0    535.507875  498.5904  463.339200  793.376200  341.124000  389.4530   
1    320.817583  405.1047  451.853300  385.929375  412.348026  475.9641   
2    395.280667  750.9708  504.672000  406.835625  677.646800  361.0307   
3    464.872333  630.1484  518.602500  509.056000  544.299395  588.7200   
4    574.060800  500.6880  493.611316  643.494375  501.307200  389.4530   
..          ...       ...         ...         ...         ...       ...   
995  539.885400  625.5678  583.949700  426.069375  513.426158  461.3800   
996  395.280667  519.1506  369.340300  755.948700  465.695100  365.3907   
997  320.817583  447.8364  498.297600  701.941000  530.765921  354.1668   
998  548.250400  520.5803  382.696263  608.175000  329.658000  427.8434   
999  464.872333  720.0475  399.510600  399.951600  661.182600  493.6520   

          CLAY   CLINTON       COLES        COOK   CRAWFORD  CUMBERLAND  \
0    318.90820  378.2076  798.220800  161.164286  357.55080  396.885600   
1    258.96750  575.2449  405.295312  288.321429  401.06055  478.667475   
2    540.68750  408.1260  526.386000  337.698900  336.22875  501.726825   
3    441.62090  426.7900  426.006000  216.462857  460.71960  362.626875   
4    365.56575  520.0188  472.221000  248.482400  443.82195  572.392575   
..         ...       ...         ...         ...        ...         ...   
995  290.88675  503.4400  440.103300  161.164286  467.22600  572.392575   
996  311.10000  418.5324  560.762437  216.036000  443.82195  501.726825   
997  510.00840  378.2076  398.200000  239.232857  418.64790  466.765875   
998  221.41350  285.9560  568.590000  316.872500  402.21480  504.071000   
999  396.13060  447.7460  637.824000  339.972000  568.05940  422.506800   

       DE KALB     DE WITT    DOUGLAS     DU PAGE       EDGAR     EDWARDS  \
0    368.84610  443.988900  448.69500  199.440000  633.090000  505.728800   
1    362.53260  413.542708  693.14350  289.366071  740.502800  312.690625   
2    760.98640  446.002200  731.97300  161.748214  656.657500  325.839667   
3    691.48960  437.304400  549.99945  308.226400  527.316075  432.635542   
4    492.54660  436.683958  570.93960  157.492400  527.316075  402.488958   
..         ...         ...        ...         ...         ...         ...   
995  539.66745  611.980000  435.46965  165.347000  462.825600  488.140800   
996  648.28380  448.148000  536.32425  278.913500  497.406150  364.324667   
997  589.11360  575.616800  416.66625  156.109286  593.587200  364.734600   
998  534.46680  417.828125  570.93960  175.993929  373.648000  312.690625   
999  453.98880  497.058400  408.91500  161.748214  439.852400  215.516000   

      EFFINGHAM     FAYETTE        FORD    FRANKLIN    FULTON    GALLATIN  \
0    509.818600  457.844400  309.017775  388.475400  367.0875  503.059200   
1    452.411812  503.007000  661.507400  379.127400  347.0616  546.585300   
2    408.388500  425.047837  433.923600  531.765500  579.4335  651.209400   
3    445.347200  335.546700  418.026000  258.576600  422.5935 

# Random:

In [28]:
aph.reset_index()

index      County     sum  count
0        0       ADAMS   948.9     20
1        1   ALEXANDER   554.6     14
2        2        BOND   780.7     18
3        3       BOONE   981.6     20
4        4       BROWN   939.5     20
..     ...         ...     ...    ...
99      99   WHITESIDE   937.4     18
100    100        WILL   956.1     20
101    101  WILLIAMSON   730.9     19
102    102   WINNEBAGO   953.7     20
103    103    WOODFORD  1118.5     20

[104 rows x 4 columns]

In [29]:
beans['bp guarantee'] = beans['County APH']*beans['Beans Base Price']
beans['hp guarantee'] = beans['County APH']*beans['Beans Harvest Price']
beans['Revenue Guarantee 75%'] = beans[['bp guarantee','hp guarantee']].max(axis = 1)*.75
beans['Revenue Guarantee 80%'] = beans[['bp guarantee','hp guarantee']].max(axis = 1)*.80
beans['Revenue Guarantee 85%'] = beans[['bp guarantee','hp guarantee']].max(axis = 1)*.85

In [30]:
aph = beans.groupby(['County'])['Value'].agg(['sum','count'])
aph

sum  count
County                   
ADAMS        948.9     20
ALEXANDER    554.6     14
BOND         780.7     18
BOONE        981.6     20
BROWN        939.5     20
...            ...    ...
WHITESIDE    937.4     18
WILL         956.1     20
WILLIAMSON   730.9     19
WINNEBAGO    953.7     20
WOODFORD    1118.5     20

[104 rows x 2 columns]

In [31]:
p_data = pd.read_csv('/Users/isaacwerries/Desktop/Price Data.csv')
del p_data['Program'], p_data['Week Ending'], p_data['Geo Level'], p_data['State ANSI'], p_data['County ANSI'], p_data['Ag District'], p_data['Ag District Code'], p_data['County'],p_data['Zip Code'], p_data['Region'], p_data['watershed_code'], p_data['Watershed'], p_data['Domain'], p_data['Domain Category'], p_data['CV (%)']
corn_p = p_data[p_data['Commodity'] == 'CORN'] #splitting the dataframe based on crop
corn_p = corn_p[corn_p['Year'] > 2000].copy()
bean_p = p_data[p_data['Commodity'] == 'SOYBEANS'].copy() #splitting the dataframe based on crop
bean_p = bean_p[bean_p['Year'] > 2000].copy()
corn_p

Year Period     State Commodity  \
0    2021    JAN  ILLINOIS      CORN   
2    2021    FEB  ILLINOIS      CORN   
4    2021    MAR  ILLINOIS      CORN   
6    2020    JAN  ILLINOIS      CORN   
8    2020    FEB  ILLINOIS      CORN   
..    ...    ...       ...       ...   
476  2001    AUG  ILLINOIS      CORN   
478  2001    SEP  ILLINOIS      CORN   
480  2001    OCT  ILLINOIS      CORN   
482  2001    NOV  ILLINOIS      CORN   
484  2001    DEC  ILLINOIS      CORN   

                                            Data Item  Value  
0    CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   4.10  
2    CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   4.69  
4    CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   4.96  
6    CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   3.76  
8    CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   3.71  
..                                                ...    ...  
476  CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   1.99  
478  CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   1.94  
480  CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   1.85  
482  CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   1.91  
484  CORN, GRAIN - PRICE RECEIVED, MEASURED IN $ / BU   2.06  

[243 rows x 6 columns]

In [ ]:
cols = brev.columns
cols = pd.DataFrame(cols)
visible = []
buttons = []
buttons = []

for column in brev.columns.to_list():
    for n in brev.columns.to_list():
        if n == column:
            j = True
        else:
            j = False
        visible.append(j)
    but = [dict(label=column, method = "restyle", args = [{'visible':visible.copy()},{'title':column,'showlegend':False}])]
    buttons.append(but.copy())
    but.clear
    visible.clear()
buttons = list(buttons)
buttons
#brev.columns.to_list()

In [53]:
fig = go.Figure()
abc = []

for column in brev.columns.to_list():
    fig.add_trace(
        go.Histogram(
            x = brev[column],
            name = 'Revenue',visible = False,nbinsx = 75))
    abc.append(column)

for column in brev75.columns.to_list():
    fig.add_trace(
        go.Histogram(
            x = brev75[column],
            name = 'Revenue with CI',visible = False,nbinsx = 75))
    abc.append(column)
    
cols = brev.columns
cols = pd.DataFrame(cols)
visible = []
buttons = []
but = []
for column in brev.columns.to_list():
    for n in abc:
        if n == column:
            j = True
        else:
            j = False
        visible.append(j)
    but = dict(label=column, method = "update", args = [{'visible':visible.copy()},{'title':column,'showlegend':True}])
    buttons.append(but.copy())
    but.clear
    visible.clear()

    
fig.update_layout(
    updatemenus=[go.layout.Updatemenu(
        active=0,
        buttons=list(buttons))])
    
fig.update_layout(barmode='overlay')
fig.update_traces(opacity=0.75)
fig.show()

In [40]:
fig = go.Figure()


fig.add_trace(go.Histogram(x = brev['MORGAN'],name = 'Revenue'))
fig.add_trace(go.Histogram(x = brev75['MORGAN'],name = 'Revenue w/ CI'))
fig.add_trace(go.Histogram(x = brev['CHAMPAIGN'],name = 'Champaign'))
    
fig.update_layout(
    updatemenus=[go.layout.Updatemenu(
        active=0,
        buttons=list(
            [dict(label = 'All',
                  method = 'update',
                  args = [{'visible': [True, True,True]},
                          {'title': 'All',
                           'showlegend':True}]),
             dict(label = 'Morgan',
                  method = 'update',
                  args = [{'visible': [True, True, False]}, # the index of True aligns with the indices of plot traces
                          {'title': 'Morgan',
                           'showlegend':True}]),
             dict(label = 'Champaign',
                  method = 'update',
                  args = [{'visible': [False, False, True]},
                          {'title': 'Champaign',
                           'showlegend':True}]),
             
            ])
        )
    ])
fig.update_layout(barmode='overlay')
fig.update_traces(opacity=0.75)

fig.show()